In [13]:
import sys
import platform
import numpy as np
import pandas as pd

print("Python version:", platform.python_version())
print("NumPy version:", np.__version__)
print("Pandas version:", pd.__version__)


Python version: 3.12.6
NumPy version: 2.1.3
Pandas version: 2.2.3


In [15]:
import pandas as pd 
import calendar
from datetime import datetime, timedelta
import numpy as np
from scipy.stats import norm
from datetime import datetime, timedelta
import calendar
import scipy.stats as si
# utilities.py
# utilities.py
import warnings
# Suppress all warnings globally
warnings.filterwarnings("ignore")
import pandas as pd
from multiprocessing import Pool, Manager
from datetime import timedelta


In [16]:
def calculate_sar(df, acceleration=0.02, maximum=0.2):
    """
    Calculate Parabolic SAR for a given dataframe containing price data.
    
    Parameters:
    df (pandas.DataFrame): DataFrame with columns 'EQ_High' and 'EQ_Low'
    acceleration (float): Starting acceleration factor (default: 0.02)
    maximum (float): Maximum acceleration factor (default: 0.2)
    
    Returns:
    dict: Dictionary containing 'SAR' and 'Trend' Series
    """
    # First rename the columns
    df = df.rename(columns={
        'EQ_Open': 'Open',
        'EQ_High': 'High',
        'EQ_Low': 'Low',
        'EQ_Close': 'Close'
    })
    
    high = df['High']
    low = df['Low']
    
    # Initialize arrays
    sar = np.zeros(len(df))
    ep = np.zeros(len(df))  # Extreme point
    af = np.zeros(len(df))  # Acceleration factor
    trend = np.zeros(len(df))  # 1 for uptrend, -1 for downtrend
    
    # Initialize first values
    trend[0] = 1  # Assume uptrend to start
    sar[0] = low[0]  # Start with first low for uptrend
    ep[0] = high[0]  # First extreme point
    af[0] = acceleration
    
    # Calculate SAR values
    for i in range(1, len(df)):
        # Previous values
        sar_prev = sar[i-1]
        ep_prev = ep[i-1]
        af_prev = af[i-1]
        trend_prev = trend[i-1]
        
        # Calculate SAR for current period
        sar[i] = sar_prev + af_prev * (ep_prev - sar_prev)
        
        # Update trend
        if trend_prev == 1:  # Previous uptrend
            trend[i] = 1
            if low[i] < sar[i]:  # Trend reversal
                trend[i] = -1
                sar[i] = ep_prev
                ep[i] = low[i]
                af[i] = acceleration
            else:
                if high[i] > ep_prev:  # New high
                    ep[i] = high[i]
                    af[i] = min(af_prev + acceleration, maximum)
                else:
                    ep[i] = ep_prev
                    af[i] = af_prev
                # Ensure SAR is below the recent lows
                sar[i] = min(sar[i], low[i-1], low[i])
                
        else:  # Previous downtrend
            trend[i] = -1
            if high[i] > sar[i]:  # Trend reversal
                trend[i] = 1
                sar[i] = ep_prev
                ep[i] = high[i]
                af[i] = acceleration
            else:
                if low[i] < ep_prev:  # New low
                    ep[i] = low[i]
                    af[i] = min(af_prev + acceleration, maximum)
                else:
                    ep[i] = ep_prev
                    af[i] = af_prev
                # Ensure SAR is above the recent highs
                sar[i] = max(sar[i], high[i-1], high[i])
    
    # Create Series for both SAR and Trend
    sar_series = pd.Series(sar, index=df.index)
    trend_series = pd.Series(trend, index=df.index)
    
    return {'SAR': sar_series, 'Trend': trend_series}

# Use the function this way:

In [17]:
############# Helper Functions ##################
def last_friday_of_previous_month(year, month):
    if month == 1:
        year -= 1
        month = 12
    else:
        month -= 1

    last_day = calendar.monthrange(year, month)[1]
    last_date = datetime(year, month, last_day)

    offset = (last_date.weekday() - 3) % 7  # 3 = Thursday
    last_thursday_date = last_date - timedelta(days=offset)
    return last_thursday_date + timedelta(days=1)  # Adjusting to Friday if needed

def last_thursday(year, month):
    last_day = calendar.monthrange(year, month)[1]
    last_date = datetime(year, month, last_day)

    offset = (last_date.weekday() - 3) % 7  # 3 = Thursday
    last_thursday_date = last_date - timedelta(days=offset)
    return last_thursday_date

def extract_strike_price_and_type(ticker):
    parts = ticker.split('-')
    strike_and_type = parts[-1]
    strike_price = ''.join([char for char in strike_and_type if char.isdigit() or char == '.'])
    option_type = 'call' if 'CE' in strike_and_type else 'put' if 'PE' in strike_and_type else None
    return float(strike_price), option_type


def calculate_historical_volatility(equity_data, lookback_period=252):
    log_returns = np.log(equity_data['EQ_Close'] / equity_data['EQ_Close'].shift(1))
    rolling_std = log_returns.rolling(window=lookback_period).std()
    volatility = rolling_std * np.sqrt(252)
    volatility = pd.Series(volatility, index=equity_data.index).fillna(0.3)
    return { 'volatility': volatility}


def calculate_time_to_maturity(current_date,lt):
    days_to_maturity = (lt - current_date).days
    return days_to_maturity / 365.0

def calculate_greeks(S, K, T, r, sigma, option_type='call'):
    d1 = (np.log(S / K) + (r + 0.5 * sigma ** 2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)

    if option_type == 'call':
        delta = si.norm.cdf(d1)
    elif option_type == 'put':
        delta = -si.norm.cdf(-d1)

    return delta

def find_option_by_delta(options_for_date, spot_price, time_to_maturity, volatility, target_delta, option_type='call'):
    options_for_date = options_for_date[options_for_date['Extracted Option Type'] == option_type]    
    options_for_date.loc[:, 'Calculated_Delta'] = options_for_date.apply(
        lambda row: calculate_greeks(spot_price, row['Strike Price'], time_to_maturity, 0.07, volatility, option_type), axis=1)
    options_for_date.loc[:, 'Delta_Diff'] = abs(options_for_date['Calculated_Delta'] - target_delta)
    if len(options_for_date) == 0:
        return None
    return options_for_date.loc[options_for_date['Delta_Diff'].idxmin()]


def get_option_price(options_data, strike_price, option_type, ohlc):
    option_row = options_data[(options_data['Strike Price'] == strike_price) & (options_data['Extracted Option Type'] == option_type)]
    return option_row[ohlc].values[0] if not option_row.empty else None


def correct_price_on_expiry(strike,spot,option_type):
    if option_type=='call':
        return max(spot-strike,0)
    if option_type=='put':
        return min(strike-spot,0)


In [ ]:
def get_data(tickers, start_year, end_year,exposure):
    option_trades=[]
    for ticker in tickers:
        stock_data=pd.read_csv(f"./Stocks Data/{ticker}_EQ_EOD.csv")

        # Use the function this way:
        result = calculate_sar(stock_data)
        stock_data['SAR'] = result['SAR']
        stock_data['Trend'] = result['Trend']
        result =calculate_historical_volatility(stock_data)
        stock_data['Volatility'] = result['volatility']
        stock_data['Date'] = pd.to_datetime(stock_data['Date']).dt.strftime('%Y-%m-%d')

        op_data=pd.read_csv(f"./Stocks Data/{ticker}_Opt_EOD.csv")
        op_data['Date'] = pd.to_datetime(op_data['Date']).dt.strftime('%Y-%m-%d')
        op_data[['Strike Price', 'Extracted Option Type']] = op_data['Ticker'].apply(extract_strike_price_and_type).apply(pd.Series)
        for year in range(start_year, end_year):
            for month in range(1, 13):
                lf=last_friday_of_previous_month(year, month)
                lt = last_thursday(year, month)

                lf_str = lf.strftime('%Y-%m-%d')
                lt_str = lt.strftime('%Y-%m-%d')
                #  Entry
                filter_stock_data = stock_data[(stock_data['Date'] >= lf_str) & (stock_data['Date'] <= lt_str)]
                filter_op_data = op_data[(op_data['Date'] >= lf_str) & (op_data['Date'] <= lt_str)]
               

                current_date = lf
                is_option_open=False
                valid_expriy_day=None 
                in_trade_option_type=None
                while current_date <= lt:
                    current_date_str=current_date.strftime('%Y-%m-%d')
                    stock_data_today=filter_stock_data[filter_stock_data['Date']==current_date_str]
                    options_data_today=filter_op_data[filter_op_data['Date']==current_date_str]
                    time_to_maturity = calculate_time_to_maturity(current_date,lt)

                    if len(stock_data_today)==0  or len(options_data_today)==0:

                        if (current_date==lt) and (valid_expriy_day!=None):
                        
                            valid_expriy_day_str=valid_expriy_day.strftime('%Y-%m-%d')
                            stock_data_today=filter_stock_data[filter_stock_data['Date']==valid_expriy_day_str]
                            options_data_today=filter_op_data[filter_op_data['Date']==valid_expriy_day_str]
                            time_to_maturity = calculate_time_to_maturity(valid_expriy_day,lt)
                            spot=stock_data_today['EQ_Close'].values[0]
                            volatility=stock_data_today['Volatility'].values[0]
                            trend=stock_data_today['Trend'].values[0]
                            option_price_close = get_option_price(options_data_today, current_position['Strike'], current_position['Option Type'], 'Close')
                            current_position['Exit Price'] = option_price_close if option_price_close is not None else correct_price_on_expiry(current_position['Strike'],spot,current_position['Option Type'])
                            current_position['Exit Delta'] = calculate_greeks(spot, current_position['Strike'], time_to_maturity, 0.07, volatility, current_position['Option Type'])
                            current_position['PNL']=(current_position['Initial Price']-current_position['Exit Price'])*current_position['Lot']
                            current_position['Exit Date']=current_date_str
                            option_trades.append(current_position.copy())
                            is_option_open=False
                        current_date+=timedelta(days=1)
                        continue

                    valid_expriy_day=current_date
                    spot=stock_data_today['EQ_Close'].values[0]
                    volatility=stock_data_today['Volatility'].values[0]
                    trend=stock_data_today['Trend'].values[0]
                    
                    if is_option_open==True:
                        now_trend='call'
                        if trend==1:
                            now_trend='put'
                        option_price_close = get_option_price(options_data_today, current_position['Strike'], current_position['Option Type'], 'Close')
                        if in_trade_option_type!=now_trend:
                            current_position['Exit Price'] = option_price_close if option_price_close is not None else current_position['Initial Price']
                            current_position['Exit Delta'] = calculate_greeks(spot, current_position['Strike'], time_to_maturity, 0.07, volatility, current_position['Option Type'])
                            current_position['PNL']=(current_position['Initial Price']-current_position['Exit Price'])*current_position['Lot']
                            current_position['Exit Date']=current_date_str
                            option_trades.append(current_position.copy())
                            is_option_open=False
                            option_target = find_option_by_delta(options_data_today, spot, time_to_maturity, volatility, 0.25 if trend == -1 else -0.25, 'call' if trend == -1 else 'put')
                            if option_target is not None:
                                option_lot_size=exposure/spot
                                current_position={
                                    'Date':current_date_str,
                                    'Entry':option_target['Ticker'],
                                    'Strike':option_target['Strike Price'],
                                    'Initial Price': option_target['Close'],
                                    'Option Type':option_target['Extracted Option Type'],
                                    'Bought Delta':option_target['Calculated_Delta'],
                                    'Lot':option_lot_size,
                                    'Expiry Month':lt.strftime('%Y-%m-%d'),
                                    'Target Delta':0.25 
                                }
                                in_trade_option_type=option_target['Extracted Option Type']
                                is_option_open=True

                        if current_date==lt:
                            option_price_close = get_option_price(options_data_today, current_position['Strike'], current_position['Option Type'], 'Close')
                            current_position['Exit Price'] = option_price_close if option_price_close is not None else correct_price_on_expiry(current_position['Strike'],spot,current_position['Option Type'])
                            current_position['Exit Delta'] = calculate_greeks(spot, current_position['Strike'], time_to_maturity, 0.07, volatility, current_position['Option Type'])
                            current_position['PNL']=(current_position['Initial Price']-current_position['Exit Price'])*current_position['Lot']
                            current_position['Exit Date']=current_date_str
                            option_trades.append(current_position.copy())
                            is_option_open=False

                    
                    if is_option_open==False:
                        option_target = find_option_by_delta(options_data_today, spot, time_to_maturity, volatility, 0.25 if trend == -1 else -0.25, 'call' if trend == -1 else 'put')
                        if option_target is not None:
                            option_lot_size=exposure/spot
                            current_position={
                                'Date':current_date_str,
                                'Entry':option_target['Ticker'],
                                'Strike':option_target['Strike Price'],
                                'Initial Price': option_target['Close'],
                                'Option Type':option_target['Extracted Option Type'],
                                'Bought Delta':option_target['Calculated_Delta'],
                                'Lot':option_lot_size,
                                'Expiry Month':lt.strftime('%Y-%m-%d'),
                                'Target Delta':0.25 
                            }
                            in_trade_option_type=option_target['Extracted Option Type']
                            is_option_open=True

                    current_date+=timedelta(days=1)
                

    return option_trades
                                                  


tickers = ['HDFCBANK']
start_year = 2019
end_year = 2025
exposure=700000

df_trades=get_data(tickers, start_year, end_year,exposure)
df=pd.DataFrame(df_trades)

df.to_csv('trades.csv', index=False)

In [28]:
# Create DataFrame
import pandas as pd
df = pd.read_csv('trades_0.5.csv')

# Extract Year and Month from Expiry Month
df['Year'] = pd.to_datetime(df['Expiry Month']).dt.year
df['Month'] = pd.to_datetime(df['Expiry Month']).dt.month

# Group by Year and Month, then sum the PNL
monthly_pnl = df.groupby(['Year', 'Month'])['PNL'].sum().reset_index()
yearly_pnl = df.groupby(['Year'])['PNL'].sum().reset_index()

yearly_pnl.to_csv('yearly_pnl.csv', index=False)
monthly_pnl.to_csv('monthly_pnl.csv', index=False)

In [29]:
# Separate "RELIANCE" from the entry details
split_data = df["Entry"].str.split("-", n=1, expand=True)
df["Symbol"] = split_data[0]
df

Date                Entry   Strike  Initial Price Option Type  \
0     2019-01-01   RELIANCE-I1129.3PE  1129.30      37.989881         put   
1     2019-01-02   RELIANCE-I1109.5CE  1109.50      29.123925        call   
2     2019-01-15   RELIANCE-I1129.3PE  1129.30      28.331437         put   
3     2019-01-30  RELIANCE-I1188.75CE  1188.75       5.398823        call   
4     2019-02-01     RELIANCE-I1268CE  1268.00      19.019706        call   
...          ...                  ...      ...            ...         ...   
8587  2024-05-07          VEDL-I400CE   400.00      14.700000        call   
8588  2024-05-14          VEDL-I435PE   435.00      16.450000         put   
8589  2024-05-31          VEDL-I454CE   454.00      25.100000        call   
8590  2024-06-20          VEDL-I474PE   474.00      12.850000         put   
8591  2024-06-28          VEDL-I460PE   460.00      25.100000         put   

      Bought Delta          Lot Expiry Month  Target Delta  Open  Exit Price  \
0        -0.494307   624.972099   2019-01-31           0.5     1   51.016399   
1         0.518372   634.230316   2019-01-31           0.5     0   36.157253   
2        -0.458782   618.948671   2019-01-31           0.5     0    0.396244   
3         0.618177   586.264657   2019-01-31           0.5     0   25.656791   
4         0.487117   558.235974   2019-02-28           0.5     1   44.577436   
...            ...          ...          ...           ...   ...         ...   
8587      0.488628  1767.453604   2024-05-30           0.5     0   38.750000   
8588     -0.494675  1616.441519   2024-05-30           0.5     0    0.000000   
8589      0.497402  1557.285873   2024-06-27           0.5     1   22.100000   
8590     -0.531161  1486.199575   2024-06-27           0.5     0   32.250000   
8591     -0.513563  1541.850220   2024-07-25           0.5     1   27.500000   

      Exit Delta           PNL   Exit Date  Year  Month    Symbol  
0      -0.564784  -8697.474311  2019-01-02  2019      1  RELIANCE  
1       0.649925  -4874.783344  2019-01-15  2019      1  RELIANCE  
2      -0.000180  17112.641050  2019-01-30  2019      1  RELIANCE  
3       1.000000 -12058.598761  2019-01-31  2019      1  RELIANCE  
4       0.620494 -14622.266346  2019-02-04  2019      2  RELIANCE  
...          ...           ...         ...   ...    ...       ...  
8587    0.892574 -43451.963136  2024-05-14  2024      5      VEDL  
8588   -0.000000  26324.558365  2024-05-30  2024      5      VEDL  
8589    0.789636   3936.818687  2024-06-20  2024      6      VEDL  
8590   -1.000000 -29502.547771  2024-06-27  2024      6      VEDL  
8591   -1.000000  -4511.453744  2024-07-25  2024      7      VEDL  

[8592 rows x 17 columns]

In [30]:
df["Date"] = pd.to_datetime(df["Date"])
df["Exit Date"] = pd.to_datetime(df["Exit Date"])

# Prepare an object grouped by dates
date_stocks = {}

for _, row in df.iterrows():
    date_range = pd.date_range(start=row["Date"], end=row["Exit Date"]).strftime('%Y-%m-%d')
    for date in date_range:
        if date not in date_stocks:
            date_stocks[date] = {"Date": date, "Stocks": [], "Put Count": 0, "Call Count": 0}
        
        # Add the stock info for the date
        date_stocks[date]["Stocks"].append({
            "Symbol": row["Symbol"],
            "Option_Type": row["Option Type"]
        })
        
        # Increment counts based on Option Type
        if row["Option Type"] == "put":
            date_stocks[date]["Put Count"] += 1
        elif row["Option Type"] == "call":
            date_stocks[date]["Call Count"] += 1

# Convert the dictionary into a list of objects
result = list(date_stocks.values())

# Display the result
for obj in result:
    print(obj)



{'Date': '2019-01-01', 'Stocks': [{'Symbol': 'RELIANCE', 'Option_Type': 'put'}, {'Symbol': 'TCS', 'Option_Type': 'put'}, {'Symbol': 'INFY', 'Option_Type': 'put'}, {'Symbol': 'HDFCBANK', 'Option_Type': 'put'}, {'Symbol': 'ICICIBANK', 'Option_Type': 'put'}, {'Symbol': 'HINDUNILVR', 'Option_Type': 'put'}, {'Symbol': 'KOTAKBANK', 'Option_Type': 'put'}, {'Symbol': 'SBIN', 'Option_Type': 'put'}, {'Symbol': 'BHARTIARTL', 'Option_Type': 'put'}, {'Symbol': 'ITC', 'Option_Type': 'put'}, {'Symbol': 'ASIANPAINT', 'Option_Type': 'put'}, {'Symbol': 'BAJFINANCE', 'Option_Type': 'put'}, {'Symbol': 'MARUTI', 'Option_Type': 'put'}, {'Symbol': 'AXISBANK', 'Option_Type': 'put'}, {'Symbol': 'LT', 'Option_Type': 'put'}, {'Symbol': 'HCLTECH', 'Option_Type': 'put'}, {'Symbol': 'SUNPHARMA', 'Option_Type': 'put'}, {'Symbol': 'WIPRO', 'Option_Type': 'put'}, {'Symbol': 'ULTRACEMCO', 'Option_Type': 'put'}, {'Symbol': 'TITAN', 'Option_Type': 'put'}, {'Symbol': 'TECHM', 'Option_Type': 'put'}, {'Symbol': 'NESTLEIND',

In [13]:
# Convert "Date" and "Exit Date" to datetime
df["Date"] = pd.to_datetime(df["Date"])
df["Exit Date"] = pd.to_datetime(df["Exit Date"])

# Prepare an object grouped by dates
date_stocks = {}

for _, row in df.iterrows():
    date_range = pd.date_range(start=row["Date"], end=row["Exit Date"]).strftime('%Y-%m-%d')
    for date in date_range:
        if date not in date_stocks:
            date_stocks[date] = {"Date": date, "Put Count": 0, "Call Count": 0}
        
        # Increment counts based on Option Type
        if row["Option Type"] == "put":
            date_stocks[date]["Put Count"] += 1
        elif row["Option Type"] == "call":
            date_stocks[date]["Call Count"] += 1

# Convert the dictionary into a list of objects
result = list(date_stocks.values())

# Display the result without the 'Stocks' key
for obj in result:
    print(obj)

ddf=pd.DataFrame(result)
ddf.to_csv('stocks_with_counts.csv', index=False)

{'Date': '2019-01-01', 'Put Count': 43, 'Call Count': 0}
{'Date': '2019-01-02', 'Put Count': 43, 'Call Count': 33}
{'Date': '2019-01-03', 'Put Count': 13, 'Call Count': 36}
{'Date': '2019-01-04', 'Put Count': 12, 'Call Count': 38}
{'Date': '2019-01-05', 'Put Count': 7, 'Call Count': 37}
{'Date': '2019-01-06', 'Put Count': 7, 'Call Count': 37}
{'Date': '2019-01-07', 'Put Count': 14, 'Call Count': 38}
{'Date': '2019-01-08', 'Put Count': 18, 'Call Count': 33}
{'Date': '2019-01-09', 'Put Count': 19, 'Call Count': 28}
{'Date': '2019-01-10', 'Put Count': 22, 'Call Count': 25}
{'Date': '2019-01-11', 'Put Count': 24, 'Call Count': 25}
{'Date': '2019-01-12', 'Put Count': 21, 'Call Count': 23}
{'Date': '2019-01-13', 'Put Count': 21, 'Call Count': 23}
{'Date': '2019-01-14', 'Put Count': 22, 'Call Count': 27}
{'Date': '2019-01-15', 'Put Count': 27, 'Call Count': 26}
{'Date': '2019-01-16', 'Put Count': 28, 'Call Count': 18}
{'Date': '2019-01-17', 'Put Count': 29, 'Call Count': 19}
{'Date': '2019-01

In [56]:
import pandas as pd


# Create DataFrame
df = pd.read_csv('./tradebooks/combined_file.csv')

df['Percentage Options Change  (%)'] = ((df['Option Initial Price']-df['Option Final Price']) / df['Option Initial Price']) * 100
df['Percentage Nifty Change  (%)'] = -((  df['Nifty Option Initial Price']-df['Nifty Option Final Price']) / df['Nifty Option Initial Price']) * 100
# Total trades

total_trades = len(df)

# Count positive and negative PNL for Options
positive_options_pnl = (df["Options PNL"] > 0).sum()
negative_options_pnl = (df["Options PNL"] <= 0).sum()

# Count positive and negative PNL for Nifty Options
positive_nifty_pnl = (df["Nifty Options PNL"] > 0).sum()
negative_nifty_pnl = (df["Nifty Options PNL"] <= 0).sum()

# Print results
print(f"Total Trades: {total_trades}")
print(f"Options PNL: {positive_options_pnl} positive, {negative_options_pnl} negative")
print(f"Nifty Options PNL: {positive_nifty_pnl} positive, {negative_nifty_pnl} negative")
df
# Separate positive and negative percentage changes for options
positive_changes = df[df['Percentage Options Change  (%)'] > 0]['Percentage Options Change  (%)'].tolist()
negative_changes = df[df['Percentage Options Change  (%)'] < 0]['Percentage Options Change  (%)'].tolist()

# Calculate averages
average_positive = sum(positive_changes) / len(positive_changes) if positive_changes else 0
average_negative = sum(negative_changes) / len(negative_changes) if negative_changes else 0

# Print results
print(f"Average of Positive Changes: {average_positive}")
print(f"Average of Negative Changes: {average_negative}")



# Separate positive and negative percentage changes for Nifty
positive_nifty_changes = df[df['Percentage Nifty Change  (%)'] > 0]['Percentage Nifty Change  (%)'].tolist()
negative_nifty_changes = df[df['Percentage Nifty Change  (%)'] < 0]['Percentage Nifty Change  (%)'].tolist()

# Calculate averages
average_positive_nifty = sum(positive_nifty_changes) / len(positive_nifty_changes) if positive_nifty_changes else 0
average_negative_nifty = sum(negative_nifty_changes) / len(negative_nifty_changes) if negative_nifty_changes else 0

# Print results
print(f"Average of Positive Nifty Changes: {average_positive_nifty}")
print(f"Average of Negative Nifty Changes: {average_negative_nifty}")




Total Trades: 22163
Options PNL: 12724 positive, 9439 negative
Nifty Options PNL: 14437 positive, 7726 negative
Average of Positive Changes: 95.35931345943563
Average of Negative Changes: -122.1939051909525
Average of Positive Nifty Changes: 260.6529760909855
Average of Negative Nifty Changes: -85.12156564765974


In [ ]:
trading_egde=((positive_options_pnl/total_trades)*average_positive)  + ((negative_options_pnl/total_trades)*average_negative)
print(trading_egde)
trading_edge_nifty=((14437/22163)*260.65)  + ((7726/22163)*-85.12)
print(trading_edge_nifty)



# trading_egde_n=negative_options_pnl/total_trades
# trading_edge_nifty_p=positive_nifty_pnl/total_trades
# trading_edge_nifty_n=negative_nifty_pnl/total_trades



2.7055738555456514
140.1143723235203


In [57]:
14437 + 7726

22163

In [ ]:
import pandas as pd
df=pd.read_csv('./tradebooks/15dte_tradebookcall.csv')

# Convert Option Close Date to datetime
df['Option Close Date'] = pd.to_datetime(df['Option Close Date'], format='%Y-%m-%d')

# Extract Year and Month
df['Year'] = df['Option Close Date'].dt.year
df['Month'] = df['Option Close Date'].dt.month

